In [2]:
import re, collections

vocab = {'l o w </w>': 5, 'l o w e r </w>': 2, 'n e w e s t </w>': 6, 'w i d e s t </w>': 3}

def get_tokens(vocab):
    tokens = collections.defaultdict(int)
    for word, freq in vocab.items():
        word_tokens = word.split()
        for token in word_tokens:
            tokens[token] += freq
    return tokens

def get_stats(vocab):
    pairs = collections.defaultdict(int)
    for word, freq in vocab.items():
        symbols = word.split()
        for i in range(len(symbols)-1):
            pairs[symbols[i],symbols[i+1]] += freq
    return pairs

def merge_vocab(pair, v_in):
    v_out = {}
    bigram = re.escape(' '.join(pair))
    p = re.compile(r'(?<!\S)' + bigram + r'(?!\S)')
    for word in v_in:
        w_out = p.sub(''.join(pair), word)
        v_out[w_out] = v_in[word]
    return v_out



print('==========')
print('Tokens Before BPE')
tokens = get_tokens(vocab)
print('Tokens: {}'.format(tokens))
print('Number of tokens: {}'.format(len(tokens)))
print('==========')

num_merges = 5
for i in range(num_merges):
    pairs = get_stats(vocab)
    if not pairs:
        break
    best = max(pairs, key=pairs.get)
    vocab = merge_vocab(best, vocab)
    print('Iter: {}'.format(i))
    print('Best pair: {}'.format(best))
    tokens = get_tokens(vocab)
    print('Tokens: {}'.format(tokens))
    print('Number of tokens: {}'.format(len(tokens)))
    print('==========')

Tokens Before BPE
Tokens: defaultdict(<class 'int'>, {'l': 7, 'o': 7, 'w': 16, '</w>': 16, 'e': 17, 'r': 2, 'n': 6, 's': 9, 't': 9, 'i': 3, 'd': 3})
Number of tokens: 11
Iter: 0
Best pair: ('e', 's')
Tokens: defaultdict(<class 'int'>, {'l': 7, 'o': 7, 'w': 16, '</w>': 16, 'e': 8, 'r': 2, 'n': 6, 'es': 9, 't': 9, 'i': 3, 'd': 3})
Number of tokens: 11
Iter: 1
Best pair: ('es', 't')
Tokens: defaultdict(<class 'int'>, {'l': 7, 'o': 7, 'w': 16, '</w>': 16, 'e': 8, 'r': 2, 'n': 6, 'est': 9, 'i': 3, 'd': 3})
Number of tokens: 10
Iter: 2
Best pair: ('est', '</w>')
Tokens: defaultdict(<class 'int'>, {'l': 7, 'o': 7, 'w': 16, '</w>': 7, 'e': 8, 'r': 2, 'n': 6, 'est</w>': 9, 'i': 3, 'd': 3})
Number of tokens: 10
Iter: 3
Best pair: ('l', 'o')
Tokens: defaultdict(<class 'int'>, {'lo': 7, 'w': 16, '</w>': 7, 'e': 8, 'r': 2, 'n': 6, 'est</w>': 9, 'i': 3, 'd': 3})
Number of tokens: 9
Iter: 4
Best pair: ('lo', 'w')
Tokens: defaultdict(<class 'int'>, {'low': 7, '</w>': 7, 'e': 8, 'r': 2, 'n': 6, 'w': 9,

+ 编码
+ 解码：将所有的 tokens 拼在一起即可

In [3]:
import re, collections

def get_vocab(filename):
    vocab = collections.defaultdict(int)
    with open(filename, 'r', encoding='utf-8') as fhand:
        for line in fhand:
            words = line.strip().split()
            for word in words:
                vocab[' '.join(list(word)) + ' </w>'] += 1

    return vocab

def get_stats(vocab):
    pairs = collections.defaultdict(int)
    for word, freq in vocab.items():
        symbols = word.split()
        for i in range(len(symbols)-1):
            pairs[symbols[i],symbols[i+1]] += freq
    return pairs

def merge_vocab(pair, v_in):
    v_out = {}
    bigram = re.escape(' '.join(pair))
    p = re.compile(r'(?<!\S)' + bigram + r'(?!\S)')
    for word in v_in:
        w_out = p.sub(''.join(pair), word)
        v_out[w_out] = v_in[word]
    return v_out

def get_tokens_from_vocab(vocab):
    tokens_frequencies = collections.defaultdict(int)
    vocab_tokenization = {}
    for word, freq in vocab.items():
        word_tokens = word.split()
        for token in word_tokens:
            tokens_frequencies[token] += freq
        vocab_tokenization[''.join(word_tokens)] = word_tokens
    return tokens_frequencies, vocab_tokenization

def measure_token_length(token):
    if token[-4:] == '</w>':
        return len(token[:-4]) + 1
    else:
        return len(token)

def tokenize_word(string, sorted_tokens, unknown_token='</u>'):
    
    if string == '':
        return []
    if sorted_tokens == []:
        return [unknown_token]

    string_tokens = []
    for i in range(len(sorted_tokens)):
        token = sorted_tokens[i]
        token_reg = re.escape(token.replace('.', '[.]'))

        matched_positions = [(m.start(0), m.end(0)) for m in re.finditer(token_reg, string)]
        if len(matched_positions) == 0:
            continue
        substring_end_positions = [matched_position[0] for matched_position in matched_positions]

        substring_start_position = 0
        for substring_end_position in substring_end_positions:
            substring = string[substring_start_position:substring_end_position]
            string_tokens += tokenize_word(string=substring, sorted_tokens=sorted_tokens[i+1:], unknown_token=unknown_token)
            string_tokens += [token]
            substring_start_position = substring_end_position + len(token)
        remaining_substring = string[substring_start_position:]
        string_tokens += tokenize_word(string=remaining_substring, sorted_tokens=sorted_tokens[i+1:], unknown_token=unknown_token)
        break
    return string_tokens

# vocab = {'l o w </w>': 5, 'l o w e r </w>': 2, 'n e w e s t </w>': 6, 'w i d e s t </w>': 3}

vocab = get_vocab('bpe_practice.txt')

print('==========')
print('Tokens Before BPE')
tokens_frequencies, vocab_tokenization = get_tokens_from_vocab(vocab)
print('All tokens: {}'.format(tokens_frequencies.keys()))
print('Number of tokens: {}'.format(len(tokens_frequencies.keys())))
print('==========')

num_merges = 10000
for i in range(num_merges):
    pairs = get_stats(vocab)
    if not pairs:
        break
    best = max(pairs, key=pairs.get)
    vocab = merge_vocab(best, vocab)
    print('Iter: {}'.format(i))
    print('Best pair: {}'.format(best))
    tokens_frequencies, vocab_tokenization = get_tokens_from_vocab(vocab)
    print('All tokens: {}'.format(tokens_frequencies.keys()))
    print('Number of tokens: {}'.format(len(tokens_frequencies.keys())))
    print('==========')

# Let's check how tokenization will be for a known word
word_given_known = 'mountains</w>'
word_given_unknown = 'Ilikeeatingapples!</w>'

sorted_tokens_tuple = sorted(tokens_frequencies.items(), key=lambda item: (measure_token_length(item[0]), item[1]), reverse=True)
sorted_tokens = [token for (token, freq) in sorted_tokens_tuple]

print(sorted_tokens)

word_given = word_given_known 

print('Tokenizing word: {}...'.format(word_given))
if word_given in vocab_tokenization:
    print('Tokenization of the known word:')
    print(vocab_tokenization[word_given])
    print('Tokenization treating the known word as unknown:')
    print(tokenize_word(string=word_given, sorted_tokens=sorted_tokens, unknown_token='</u>'))
else:
    print('Tokenizating of the unknown word:')
    print(tokenize_word(string=word_given, sorted_tokens=sorted_tokens, unknown_token='</u>'))

word_given = word_given_unknown 

print('Tokenizing word: {}...'.format(word_given))
if word_given in vocab_tokenization:
    print('Tokenization of the known word:')
    print(vocab_tokenization[word_given])
    print('Tokenization treating the known word as unknown:')
    print(tokenize_word(string=word_given, sorted_tokens=sorted_tokens, unknown_token='</u>'))
else:
    print('Tokenizating of the unknown word:')
    print(tokenize_word(string=word_given, sorted_tokens=sorted_tokens, unknown_token='</u>'))

Tokens Before BPE
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'a', 'r', 's', 'g', 'o', 't', 'h', 'l', 'd', 'u', 'n', 'b', 'i', 'x', 'p', 'm', 'v', ',', 'c', '.', 'T', 'B', 'L', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 'W', 'j', '!', 'P', 'k', 'H', 'z', "'", '2', '8', '°', 'q', '1', '0', 'D', 'F', '_', 'S', ':', '-', '9', '5', ';', '3', '4', '7', '6', 'J', '?', 'Q'])
Number of tokens: 68
Iter: 0
Best pair: ('e', '</w>')
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'a', 'r', 's', 'g', 'o', 't', 'h', 'e</w>', 'l', 'd', 'u', 'n', 'b', 'i', 'x', 'p', 'm', 'v', ',', 'c', '.', 'T', 'B', 'L', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 'W', 'j', '!', 'P', 'k', 'H', 'z', "'", '2', '8', '°', 'q', '1', '0', 'D', 'F', '_', 'S', ':', '-', '9', '5', ';', '3', '4', '7', '6', 'J', '?', 'Q'])
Number of tokens: 69
Iter: 1
Best pair: ('t', 'h')
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'a', 'r', 's', 'g', 'o', 'th', 'e</w>', 'l', 'd', 'u', 'n', 't', 'b', 'h', 'i'

Iter: 49
Best pair: ('en', '</w>')
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'ar', 's</w>', 'a', 'g', 'o</w>', 'the</w>', 'or', 'l', 'd</w>', 'as</w>', 'su', 'd', 'en', 'y</w>', 'st', 'ou', 'n', 'ed</w>', 'b', 'h', 'ing</w>', 'of</w>', 'an', 'x', 'p', 'er', 'i', 'm', 't</w>', 'a</w>', 'o', 's', 'v', 'el', 'and</w>', 'at', 'u', 're', ',</w>', 'al', 't', 'th', 'er</w>', 'c', 'in</w>', '.</w>', 'Th', 'e</w>', 'B', 'L', 'T', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 'ti', 'll', 'en</w>', 'ic', 'r', 'at</w>', 'W', 'on', 'es', 'is', 'om', 'on</w>', 'j', 'ec', '!', 'P', 'in', 'or</w>', 'e,</w>', 'it', 'k', 'f</w>', 'to</w>', 'H', 'z', 'ac', "'", '2', '8', '°', 'q', '1', ',', '0', 'D', 'F', '_', 'S', 'ing', ':', '-', '9', '5', ';', '3', '4', '7', '6', 'J', '.', '?', 'Q'])
Number of tokens: 118
Iter: 50
Best pair: ('r', 'o')
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'ar', 's</w>', 'a', 'g', 'o</w>', 'the</w>', 'or', 'l', 'd</w>', 'as</w>', 'su', 'd', 'en', 'y</w>'

Iter: 107
Best pair: ('ro', 'jec')
All tokens: dict_keys(['A', '</w>', 'f', 'e', 'w', 'y', 'ar', 's</w>', 'a', 'g', 'o</w>', 'the</w>', 'or', 'ld</w>', 'was</w>', 'su', 'd', 'en', 'ly</w>', 'st', 'oun', 'ed</w>', 'by</w>', 'h', 'ing</w>', 'of</w>', 'an</w>', 'x', 'p', 'er', 'im', 'ent</w>', 'a</w>', 'm', 'o', 'st</w>', 'no', 'v', 'el', 'and</w>', 'n', 'at', 'u', 're', ',</w>', 'al', 't', 'th', 'er</w>', 'un', 'c', 'ed', 'ent', 'in</w>', 'an', 's', 'i', '.</w>', 'The</w>', 'B', 'L', 'T', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 'et', 'y</w>', 'ti', 'll', 'en</w>', 'ic', 'ur', 'at</w>', 'iv', 'il', 'W', 'had</w>', 'con', 'de', 'l', 'es', 'bl', 'is', 'di', 't</w>', 'om', 'ati', 'on</w>', 'with</w>', 'Mo', 'rojec', 'til', '!', 'P', 'si', 'b', 'ig', 'in', 'or</w>', 'r', 'e,</w>', 'on', 'ou', 'it', 'am', 'ri', 'e</w>', 'k', 'f</w>', 'to</w>', 'ro', 'all', 'ec', 'H', 'z', 's,</w>', 'ac', "'", 'be</w>', '2', '8', '°', 'th</w>', 'q', 'that</w>', 'it</w>', 'ver', 'bu', 'al</w>', '1', ',', '0

All tokens: dict_keys(['A', '</w>', 'fe', 'w', 'y', 'ear', 's</w>', 'a', 'g', 'o</w>', 'the</w>', 'or', 'ld</w>', 'was</w>', 'su', 'd', 'en', 'ly</w>', 'ast', 'oun', 'ded</w>', 'by</w>', 'h', 'ing</w>', 'of</w>', 'an</w>', 'ex', 'p', 'er', 'im', 'ent</w>', 'a</w>', 'mo', 'st</w>', 'no', 'v', 'el', 'and</w>', 'dar', 'n', 'at', 'u', 're', ',</w>', 'al', 't', 'o', 'e', 'ther</w>', 'un', 'pre', 'c', 'ed', 'ent', 'ed</w>', 'in</w>', 'ann', 'sc', 'i', 'e.</w>', 'The</w>', 'B', 'L', 'T', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 's', 'et', 'y</w>', 'ar', 'ti', 'll', 'm', 'en</w>', 'st', 'ted</w>', 'ic', 'ur', 'at</w>', 'iv', 'il', 'W', 'had</w>', 'conc', 'de', 'th', 'l', 'es', 'bl', 'is', 'di', 't</w>', 'com', 'ati', 'on</w>', 'with</w>', 'Moon</w>', 'an', 'rojectil', '!', 'P', 'si', 'b', 'ig', 'in', 'or</w>', 'pr', 'e,</w>', 'r', 'on', 'our', 'its</w>', 'f', 'ea', 'it', 'om', 'am', 'ri', 'e</w>', 'y,</w>', 'k</w>', 'f</w>', 'to</w>', 'pro', 'id', 'all', 'ec', 'ess', '.</w>', 'H', 'z', 'ic

Iter: 234
Best pair: ('su', 'r')
All tokens: dict_keys(['A', '</w>', 'fe', 'w', 'y', 'ear', 's</w>', 'a', 'g', 'o</w>', 'the</w>', 'wor', 'ld</w>', 'was</w>', 'su', 'd', 'en', 'ly</w>', 'ast', 'oun', 'ded</w>', 'by</w>', 'h', 'ing</w>', 'of</w>', 'an</w>', 'ex', 'per', 'im', 'ent</w>', 'a</w>', 'mo', 'st</w>', 'no', 'v', 'el', 'and</w>', 'dar', 'n', 'at', 'u', 're', ',</w>', 'al', 't', 'o', 'e', 'ther</w>', 'un', 'pre', 'c', 'ed', 'ent', 'ed</w>', 'in</w>', 'ann', 'sc', 'i', 'e.</w>', 'The</w>', 'B', 'L', 'T', 'I', 'M', 'O', 'R', 'E', 'G', 'U', 'N', 'C', 's', 'et', 'y</w>', 'ar', 'ti', 'll', 'er', 'm', 'en</w>', 'st', 'ted</w>', 'ic', 'ur', 'great</w>', 'iv', 'il', 'W', 'had</w>', 'conc', 'de', 'th', 'l', 'es', 'bl', 'is', 'di', 't</w>', 'com', 'ati', 'on</w>', 'with</w>', 'Moon</w>', 'me', 'an', 'p', 'rojectil', '!', 'P', 'si', 'Barbic', 'or', 'ig', 'in', 'or</w>', 'pr', 'e,</w>', 'r', 'ong', 'our', 'its</w>', 'f', 'ea', 'b', 'it', 'on', 'om', 'ers</w>', 'am', 'ri', 'ge</w>', 'bs', 'y

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Best pair: ('advent', 'ur')
All tokens: dict_keys(['A</w>', 'few</w>', 'years</w>', 'ago</w>', 'the</w>', 'world</w>', 'was</w>', 'suddenly</w>', 'astounded</w>', 'by</w>', 'hearing</w>', 'of</w>', 'an</w>', 'experiment</w>', 'a</w>', 'most</w>', 'novel</w>', 'and</w>', 'daring</w>', 'nature,</w>', 'altogether</w>', 'unprecedented</w>', 'in</w>', 'annals</w>', 'science.</w>', 'The</w>', 'BALTIMORE</w>', 'GUN</w>', 'CLUB,</w>', 'society</w>', 'artillerymen</w>', 'started</w>', 'America</w>', 'during</w>', 'great</w>', 'Civil</w>', 'War,</w>', 'had</w>', 'conceived</w>', 'idea</w>', 'nothing</w>', 'less</w>', 'than</w>', 'establishing</w>', 'direct</w>', 'communication</w>', 'with</w>', 'Moon</w>', 'means</w>', 'projectile!</w>', 'President</w>', 'Barbican,</w>', 'originator</w>', 'enterprise,</w>', 'strongly</w>', 'encouraged</w>', 'its</w>', 'feasibility</w>', 'astronomers</w>', 'Cambridge</w>', 'Observatory,</w>', 'took</w>', 'upon</w>', 'himself</w>', 'to</w>', 'provide</w>', 'all</

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Number of tokens: 909
Iter: 2061
Best pair: ('dramatic', '</w>')
All tokens: dict_keys(['A</w>', 'few</w>', 'years</w>', 'ago</w>', 'the</w>', 'world</w>', 'was</w>', 'suddenly</w>', 'astounded</w>', 'by</w>', 'hearing</w>', 'of</w>', 'an</w>', 'experiment</w>', 'a</w>', 'most</w>', 'novel</w>', 'and</w>', 'daring</w>', 'nature,</w>', 'altogether</w>', 'unprecedented</w>', 'in</w>', 'annals</w>', 'science.</w>', 'The</w>', 'BALTIMORE</w>', 'GUN</w>', 'CLUB,</w>', 'society</w>', 'artillerymen</w>', 'started</w>', 'America</w>', 'during</w>', 'great</w>', 'Civil</w>', 'War,</w>', 'had</w>', 'conceived</w>', 'idea</w>', 'nothing</w>', 'less</w>', 'than</w>', 'establishing</w>', 'direct</w>', 'communication</w>', 'with</w>', 'Moon</w>', 'means</w>', 'projectile!</w>', 'President</w>', 'Barbican,</w>', 'originator</w>', 'enterprise,</w>', 'strongly</w>', 'encouraged</w>', 'its</w>', 'feasibility</w>', 'astronomers</w>', 'Cambridge</w>', 'Observatory,</w>', 'took</w>', 'upon</w>', 'himself<

[]


In [1]:
import re, collections

vocab = {'i t </w>': 5, 't h e m </w>': 2, 'h e r </w>': 6, 't h e </w>': 3}

def get_tokens(vocab):
    tokens = collections.defaultdict(int)
    for word, freq in vocab.items():
        word_tokens = word.split()
        for token in word_tokens:
            tokens[token] += freq
    return tokens

def get_stats(vocab):
    pairs = collections.defaultdict(int)
    for word, freq in vocab.items():
        symbols = word.split()
        for i in range(len(symbols)-1):
            pairs[symbols[i],symbols[i+1]] += freq
    return pairs

def merge_vocab(pair, v_in):
    v_out = {}
    bigram = re.escape(' '.join(pair))
    p = re.compile(r'(?<!\S)' + bigram + r'(?!\S)')
    for word in v_in:
        w_out = p.sub(''.join(pair), word)
        v_out[w_out] = v_in[word]
    return v_out



print('==========')
print('Tokens Before BPE')
tokens = get_tokens(vocab)
print('Tokens: {}'.format(tokens))
print('Number of tokens: {}'.format(len(tokens)))
print('==========')

num_merges = 5
for i in range(num_merges):
    pairs = get_stats(vocab)
    if not pairs:
        break
    best = max(pairs, key=pairs.get)
    vocab = merge_vocab(best, vocab)
    print('Iter: {}'.format(i))
    print('Best pair: {}'.format(best))
    tokens = get_tokens(vocab)
    print('Tokens: {}'.format(tokens))
    print('Number of tokens: {}'.format(len(tokens)))
    print('==========')

Tokens Before BPE
Tokens: defaultdict(<class 'int'>, {'i': 5, 't': 10, '</w>': 16, 'h': 11, 'e': 11, 'm': 2, 'r': 6})
Number of tokens: 7
Iter: 0
Best pair: ('h', 'e')
Tokens: defaultdict(<class 'int'>, {'i': 5, 't': 10, '</w>': 16, 'he': 11, 'm': 2, 'r': 6})
Number of tokens: 6
Iter: 1
Best pair: ('he', 'r')
Tokens: defaultdict(<class 'int'>, {'i': 5, 't': 10, '</w>': 16, 'he': 5, 'm': 2, 'her': 6})
Number of tokens: 6
Iter: 2
Best pair: ('her', '</w>')
Tokens: defaultdict(<class 'int'>, {'i': 5, 't': 10, '</w>': 10, 'he': 5, 'm': 2, 'her</w>': 6})
Number of tokens: 6
Iter: 3
Best pair: ('i', 't')
Tokens: defaultdict(<class 'int'>, {'it': 5, '</w>': 10, 't': 5, 'he': 5, 'm': 2, 'her</w>': 6})
Number of tokens: 6
Iter: 4
Best pair: ('it', '</w>')
Tokens: defaultdict(<class 'int'>, {'it</w>': 5, 't': 5, 'he': 5, 'm': 2, '</w>': 5, 'her</w>': 6})
Number of tokens: 6
